In [1]:
from structures import *
from utils import *
import random

In [2]:
class Node:
    def __init__(self):
        self.parent = None
        self.leaf = True
        self.keys = []
        self.pointers = [None]
        self.max_keys = 3
        self.min_leaf_keys = (self.max_keys + 1) // 2
        self.min_non_leaf_keys = self.max_keys // 2

In [3]:
_="""
We will assume, that the key is not present into the list
Start from root node, perform exact match for key as ‘key’ till a leaf node. Let the search path
be x1, x2, … , xh. The x1 is first node so root, then xh is leaf node. Each node xi is parent of xi+1
Insert the new object where key is ‘key’, and value is v into xh.
i := h
while xi overflows, do
   divide xi into two nodes, by moving the larger half of the keys into a new node p.
   if xi is leaf node, link p into the linked list among leaf nodes.
   identify a key k, to be inserted into the parent level along with child pointer pointing p.
   The choice of k depends on the type of the node xi. If xi is leaf node, we will perform
   copy up. So smallest key in p, is copied as k to the parent level. On the other hand, if xi is
   non-leaf node, then we will perform push up. So smallest key in p, will be copied into k,
   in the parent node.
   if i = 0, then
      create a new index node as the new root. In the new root store node with key k,
      and two child xi and p.
      return
   else
      insert a key k and a child pointer pointing to p, into node xi-1.
      i := i – 1
   end if
done
"""

In [4]:
def get_right_sibling(node):
    if node.parent == None:
        return None
    for i in range(len(node.parent.pointers)-1): # skip the last as if node is last pointer then no right sibling
        if node.parent.pointers[i] is node:
            return node.parent.pointers[i+1]
    return None

In [5]:
def get_left_sibling(node):
    if node.parent == None:
        return None
    for i in range(1, len(node.parent.pointers)): # skip the first as if node is first pointer then no left sibling
        if node.parent.pointers[i] is node:
            return node.parent.pointers[i-1]
    return None

In [6]:
def delete(node, key):
    delete_helper(node, key)
    if node.pointers[0] == None:
        print("tree is empty")
        return node
    if len(node.keys) == 0:
        print("root has no keys, updating root!")
        node.pointers[0].parent = None
        return node.pointers[0]
    return node

In [7]:
def delete_helper(node, key):
    if node.leaf:
        for i in range(len(node.keys)):
            if node.keys[i] == key:
                node.keys.pop(i)
                node.pointers.pop(i)
                next_largest = node.keys[i] if i < len(node.keys) else None
                break
        
        if next_largest == None:
            next_largest = node.pointers[-1].keys[0] if node.pointers[-1] else None
        
        if node.parent == None:
            return False, next_largest
        
        if len(node.keys) >= node.min_leaf_keys:
            return False, next_largest
        
        print("Leaf underflow")
        # check if can borrow from left sibling
        left_sibling = get_left_sibling(node)
        if left_sibling and len(left_sibling.keys) > node.min_leaf_keys:
            print("Leaf borrow from left")
            leaf_distribute(left_sibling, node)
            return False, next_largest
        
        # check if can borrow from right sibling
        right_sibling = get_right_sibling(node)
        if right_sibling and len(right_sibling.keys) > node.min_leaf_keys:
            print("Leaf borrow from right")
            leaf_distribute(node, right_sibling)
            return False, next_largest
        
        # check if can merge with left sibling
        if left_sibling:
            print("Leaf merge with left")
            leaf_merge(left_sibling, node)
            return True, next_largest
        
        # check if can merge with right sibling
        if right_sibling:
            print("Leaf merge with right")
            leaf_merge(node, right_sibling)
            return True, next_largest
        
        raise Exception("Leaf deletion underflow could never borrow nor merge")
            
    elif not node.leaf:
        deleted = False
        for i in range(len(node.keys)):
            if key < node.keys[i]:
                pos = i
                res = delete_helper(node.pointers[i], key)
                deleted = True
                break
        
        if not deleted:
            pos = len(node.pointers) - 1
            res = delete_helper(node.pointers[-1], key)
        
        if res[0] == False or len(node.keys) >= node.min_non_leaf_keys or node.parent == None:
            replace_key(node, key, res[1])
            return False, res[1]
            
        print("Non leaf underflow")
        # check if can borrow from left sibling
        left_sibling = get_left_sibling(node)
        if left_sibling and len(left_sibling.keys) > node.min_non_leaf_keys:
            print("Non leaf borrow from left")
            distribute(left_sibling, node)
            replace_key(node, key, res[1])
            return False, res[1]
        
        right_sibling = get_right_sibling(node)
        if right_sibling and len(right_sibling.keys) > node.min_non_leaf_keys:
            print("Non leaf borrow from right")
            distribute(node, right_sibling)
            replace_key(node, key, res[1])
            return False, res[1]
        
        # check if can merge with left sibling
        if left_sibling:
            print("Non leaf merge with left")
            merge_with_left(left_sibling, node)
            replace_key(node, key, res[1])
            return True, res[1]
        
        # check if can merge with right sibling
        if right_sibling:
            print("Non leaf merge with right")
            merge_with_right(node, right_sibling)
            replace_key(node, key, res[1])
            return True, res[1]
        

        raise Exception("Non leaf deletion underflow could never borrow nor merge")
            
        

In [8]:
def replace_key(node, old, new):
    if new == None:
        return
    for i in range(len(node.keys)):
        if node.keys[i] == old:
            node.keys[i] = new

In [9]:
def leaf_distribute(left, right):
#     print("leaf_distribute")
    all_keys = left.keys + right.keys
    all_pointers = left.pointers[:-1] + right.pointers[:-1]
    num_left = (len(all_keys) + 1) // 2

    left.keys = all_keys[:num_left]
    left.pointers = all_pointers[:num_left] + [left.pointers[-1]]

    right.keys = all_keys[num_left:]
    right.pointers = all_pointers[num_left:] + [right.pointers[-1]]
    
    update_parent_lb(left)
    update_parent_lb(right)

In [10]:
def update_parent_lb(node):
    for i in range(1, len(node.parent.pointers)):
        if node.parent.pointers[i] is node:
            node.parent.keys[i-1] = node.keys[0]

In [11]:
def leaf_merge(left, right):
#     print("leaf_merge")
    left.keys.extend(right.keys)
    left.pointers.pop()
    left.pointers.extend(right.pointers)
    remove_from_parent_next_pointer_and_key(left)
    update_parent_lb(left)

In [12]:
def remove_from_parent_next_pointer_and_key(node):
    for i in range(len(node.parent.pointers)-1):
        if node.parent.pointers[i] is node:
            node.parent.pointers.pop(i+1)
            return node.parent.keys.pop(i)
        
def remove_from_parent_prev_pointer_and_key(node):
    for i in range(1, len(node.parent.pointers)):
        if node.parent.pointers[i] is node:
            node.parent.pointers.pop(i-1)
            return node.parent.keys.pop(i-1)

In [13]:
def distribute(left, right):
#     print("distribute")
    parent = left.parent
    pivot_pos = None
    for i in range(len(parent.pointers)):
        if parent.pointers[i] is left:
            pivot_pos = i
    if pivot_pos == None or pivot_pos == len(parent.pointers) - 1:
        print("pivot_pos:", pivot_pos)
        raise Exception("If left has a right sibling, it must have a pivot_pos < len(parent.pointers) - 1")
    assert parent.pointers[pivot_pos+1] is right
    
    num_left = (len(right.keys) + len(left.keys) + 1) // 2
    num_right = (len(right.keys) + len(left.keys)) - num_left
    
    for _ in range(num_left - len(left.keys)):
        left.keys.append(parent.keys[pivot_pos])
        parent.keys[pivot_pos] = right.keys.pop(0)
        left.pointers.append(right.pointers.pop(0))
        left.pointers[-1].parent = left
        left.keys[-1] = left.pointers[-1].keys[0]
    
    for _ in range(num_right - len(right.keys)):
        right.keys.insert(0, parent.keys[pivot_pos])
        parent.keys[pivot_pos] = left.keys.pop()
        right.pointers.insert(0, left.pointers.pop())
        right.pointers[0].parent = right


In [14]:
def merge_with_right(node, right):
    x = remove_from_parent_next_pointer_and_key(node)
    node.keys.append(x)
    for i in range(len(right.pointers)):
        node.pointers.append(right.pointers[i])
        node.pointers[-1].parent = node
#         node.keys[-1] = node.pointers[-1].keys[0]
        if i == len(right.keys):
            break
        node.keys.append(right.keys[i])

def merge_with_left(left, node):
    x = remove_from_parent_prev_pointer_and_key(node)
    node.keys.insert(0, x)
    # right.keys[0] = right.pointers[0].keys[0]
    while left.pointers:
        node.pointers.insert(0, left.pointers.pop())
        node.pointers[0].parent = node
        if left.keys:
            node.keys.insert(0, left.keys.pop())

In [15]:
_="""
We will assume, that the key is present into the list
Start from root node, perform exact match for key as ‘key’ till a leaf node. Let the search path
be x1, x2, … , xh. The x1 is first node so root, then xh is leaf node. Each node xi is parent of xi+1
delete the object where key is ‘key’ from xh.
if h = 1, then return, as there is only one node which is root.
i := h
while xi underflows, do
   if immediate sibling node s of xi, has at least m/2 + 1 elements, then
      redistribute entries evenly between s and xi.
      corresponding to redistribution, a key k in the parent node xi-1, will be changed.
      if xi is non-leaf node, then
         k is dragged down to xi. and a key from s is pushed up to fill the place of k
      else
         k is simply replaced by a key in s
      return
   else
      merge xi with the sibling node s. Delete the corresponding child pointer in xi-1.
      if xi is an internal node, then
         drag the key in xi-1. which is previously divides xi and s. into the new node
         xi and s, into the new node xi.
      else
         delete that key in xi-1.
      i := i – 1
   end if
done
"""

In [16]:
def insert_helper(node, key, value):
    if node.leaf:
        inserted = False
        for i in range(len(node.keys)):
            if key < node.keys[i]:
                node.keys.insert(i, key)
                node.pointers.insert(i, value)
                inserted = True
                break
        if not inserted:
            node.pointers.insert(len(node.keys), value)
            node.keys.insert(len(node.keys), key)
        if len(node.keys) > node.max_keys:
            num_left = (len(node.keys) + 1) // 2
            
            right_node = Node()
            right_node.keys = node.keys[num_left:]
            right_node.pointers = node.pointers[num_left:-1] + [None]
            
            node.keys = node.keys[:num_left]
            node.pointers = node.pointers[:num_left] + [right_node]
            
            to_insert = Node()
            to_insert.leaf = False
            to_insert.keys = [right_node.keys[0]]
            to_insert.pointers = [node, right_node]
            
            node.parent = to_insert
            right_node.parent = to_insert
            
            return to_insert
        return None
        
    elif not node.leaf:
        inserted = False
        for i in range(len(node.keys)):
            if key < node.keys[i]:
                pos = i
                res = insert_helper(node.pointers[i], key, value)
                inserted = True
                break
        if not inserted:
            pos = len(node.pointers) - 1
            res = insert_helper(node.pointers[-1], key, value)
        if res == None:
            return None
        node.keys.insert(pos, res.keys[0])
        node.pointers[pos] = res.pointers[0]
        node.pointers.insert(pos+1, res.pointers[1])
        node.pointers[pos].parent = node
        node.pointers[pos+1].parent = node
        
        if len(node.keys) > node.max_keys:
            num_left = len(node.keys) // 2
            
            right_node = Node()
            right_node.leaf = False
            right_node.keys = node.keys[num_left+1:]
            right_node.pointers = node.pointers[num_left+1:]
            for pointer in right_node.pointers:
                pointer.parent = right_node
            
            to_insert = Node()
            to_insert.leaf = False
            to_insert.keys = [node.keys[num_left]]
            to_insert.pointers = [node, right_node]
            
            node.keys = node.keys[:num_left]
            node.pointers = node.pointers[:num_left+1]
            
            node.parent = to_insert
            right_node.parent = to_insert
            
            return to_insert
        return None

In [17]:
def insert(root, key, value):
    res = insert_helper(root, key, value)
    return res if res else root

In [18]:
def show(root):
    cur = [root]
    while cur:
        nxt = []
        to_print = []
        for node in cur:
            if node == None:
                print("Empty tree")
                return
            for key in node.keys:
                to_print.append(key)
            to_print.append("|")
            for pointer in node.pointers:
                if type(pointer) != Node:
                    break
                nxt.append(pointer)
        print(" ".join(str(x) for x in to_print))
        print()
        cur = nxt

In [19]:
def validate_parent(root):
    for p in root.pointers:
        if type(p) == Node:
            assert p.parent is root
            validate_parent(p)
        else:
            return

In [20]:
def validate(root):
    if root.parent != None:
        if root.leaf:
            assert root.min_leaf_keys <= len(root.keys) <= root.max_keys
        else:
            assert root.min_non_leaf_keys <= len(root.keys) <= root.max_keys
    for i in range(len(root.keys)-1):
        assert root.keys[i] < root.keys[i+1]
    if type(root.pointers[0]) != Node:
        return root.pointers[0]
    for i in range(len(root.pointers)-1):
        assert root.pointers[i].keys[0] < root.pointers[i+1].keys[0]
    for i in range(len(root.pointers)):
        if i > 0:
            assert root.keys[i-1] == validate(root.pointers[i])
        else:
            validate(root.pointers[i])
    return validate(root.pointers[0])

In [21]:
while True:
    root = Node()
    arr = list(range(24))
    random.shuffle(arr)
    print("insertion:", arr)
    for i in arr:
        root = insert(root, i, i)
        validate(root)
        validate_parent(root)
    random.shuffle(arr)
    print("deletion:", arr)
    for i in arr:
        print("Delete:", i)
        root = delete(root, i)
        show(root)
        validate(root)
        validate_parent(root)

insertion: [15, 6, 21, 3, 1, 5, 12, 11, 10, 9, 16, 2, 22, 0, 23, 17, 13, 7, 8, 20, 4, 14, 19, 18]
deletion: [14, 11, 22, 1, 18, 13, 10, 0, 15, 20, 19, 2, 8, 21, 16, 3, 12, 6, 23, 17, 7, 5, 4, 9]
Delete: 14
Leaf underflow
Leaf merge with left
7 11 17 |

2 5 | 9 | 15 | 19 21 |

0 1 | 2 3 4 | 5 6 | 7 8 | 9 10 | 11 12 13 | 15 16 | 17 18 | 19 20 | 21 22 23 |

Delete: 11
7 12 17 |

2 5 | 9 | 15 | 19 21 |

0 1 | 2 3 4 | 5 6 | 7 8 | 9 10 | 12 13 | 15 16 | 17 18 | 19 20 | 21 22 23 |

Delete: 22
7 12 17 |

2 5 | 9 | 15 | 19 21 |

0 1 | 2 3 4 | 5 6 | 7 8 | 9 10 | 12 13 | 15 16 | 17 18 | 19 20 | 21 23 |

Delete: 1
Leaf underflow
Leaf borrow from right
7 12 17 |

3 5 | 9 | 15 | 19 21 |

0 2 | 3 4 | 5 6 | 7 8 | 9 10 | 12 13 | 15 16 | 17 18 | 19 20 | 21 23 |

Delete: 18
Leaf underflow
Leaf merge with right
7 12 17 |

3 5 | 9 | 15 | 21 |

0 2 | 3 4 | 5 6 | 7 8 | 9 10 | 12 13 | 15 16 | 17 19 20 | 21 23 |

Delete: 13
Leaf underflow
Leaf merge with right
Non leaf underflow
Non leaf merge with left
7 17 |

Leaf underflow
Leaf merge with left
7 14 20 |

3 5 | 10 | 18 | 22 |

0 1 2 | 3 4 | 5 6 | 7 8 9 | 10 11 12 | 14 15 16 | 18 19 | 20 21 | 22 23 |

Delete: 12
7 14 20 |

3 5 | 10 | 18 | 22 |

0 1 2 | 3 4 | 5 6 | 7 8 9 | 10 11 | 14 15 16 | 18 19 | 20 21 | 22 23 |

Delete: 1
7 14 20 |

3 5 | 10 | 18 | 22 |

0 2 | 3 4 | 5 6 | 7 8 9 | 10 11 | 14 15 16 | 18 19 | 20 21 | 22 23 |

Delete: 3
Leaf underflow
Leaf merge with left
7 14 20 |

5 | 10 | 18 | 22 |

0 2 4 | 5 6 | 7 8 9 | 10 11 | 14 15 16 | 18 19 | 20 21 | 22 23 |

Delete: 22
Leaf underflow
Leaf merge with left
Non leaf underflow
Non leaf merge with left
7 14 |

5 | 10 | 18 20 |

0 2 4 | 5 6 | 7 8 9 | 10 11 | 14 15 16 | 18 19 | 20 21 23 |

Delete: 23
7 14 |

5 | 10 | 18 20 |

0 2 4 | 5 6 | 7 8 9 | 10 11 | 14 15 16 | 18 19 | 20 21 |

Delete: 21
Leaf underflow
Leaf merge with left
7 14 |

5 | 10 | 18 |

0 2 4 | 5 6 | 7 8 9 | 10 11 | 14 15 16 | 18 19 20 |

Delete: 8
7 14 |

5 | 10 | 18 |

0 2 4 | 5 6 | 7 9 | 10 11 | 14 15 16 | 18 19 20 |

Dele

Delete: 11
9 15 |

4 7 | 12 | 18 21 |

2 3 | 4 5 6 | 7 8 | 9 10 | 12 13 | 15 16 17 | 18 19 20 | 21 22 |

Delete: 17
9 15 |

4 7 | 12 | 18 21 |

2 3 | 4 5 6 | 7 8 | 9 10 | 12 13 | 15 16 | 18 19 20 | 21 22 |

Delete: 3
Leaf underflow
Leaf borrow from right
9 15 |

5 7 | 12 | 18 21 |

2 4 | 5 6 | 7 8 | 9 10 | 12 13 | 15 16 | 18 19 20 | 21 22 |

Delete: 18
9 15 |

5 7 | 12 | 19 21 |

2 4 | 5 6 | 7 8 | 9 10 | 12 13 | 15 16 | 19 20 | 21 22 |

Delete: 19
Leaf underflow
Leaf merge with left
9 15 |

5 7 | 12 | 21 |

2 4 | 5 6 | 7 8 | 9 10 | 12 13 | 15 16 20 | 21 22 |

Delete: 4
Leaf underflow
Leaf merge with right
9 15 |

7 | 12 | 21 |

2 5 6 | 7 8 | 9 10 | 12 13 | 15 16 20 | 21 22 |

Delete: 16
9 15 |

7 | 12 | 21 |

2 5 6 | 7 8 | 9 10 | 12 13 | 15 20 | 21 22 |

Delete: 21
Leaf underflow
Leaf merge with left
Non leaf underflow
Non leaf merge with left
9 |

7 | 12 15 |

2 5 6 | 7 8 | 9 10 | 12 13 | 15 20 22 |

Delete: 7
Leaf underflow
Leaf borrow from left
9 |

6 | 12 15 |

2 5 | 6 8 | 9 10 | 1

4 6 | 11 | 18 20 |

0 1 | 4 5 | 6 7 8 | 9 10 | 11 13 | 14 16 | 18 19 | 20 23 |

Delete: 11
Leaf underflow
Leaf merge with left
Non leaf underflow
Non leaf borrow from left
6 14 |

4 | 9 | 18 20 |

0 1 | 4 5 | 6 7 8 | 9 10 13 | 14 16 | 18 19 | 20 23 |

Delete: 4
Leaf underflow
Leaf merge with left
Non leaf underflow
Non leaf merge with right
14 |

6 9 | 18 20 |

0 1 5 | 6 7 8 | 9 10 13 | 14 16 | 18 19 | 20 23 |

Delete: 1
14 |

6 9 | 18 20 |

0 5 | 6 7 8 | 9 10 13 | 14 16 | 18 19 | 20 23 |

Delete: 6
14 |

7 9 | 18 20 |

0 5 | 7 8 | 9 10 13 | 14 16 | 18 19 | 20 23 |

Delete: 23
Leaf underflow
Leaf merge with left
14 |

7 9 | 18 |

0 5 | 7 8 | 9 10 13 | 14 16 | 18 19 20 |

Delete: 0
Leaf underflow
Leaf merge with right
14 |

9 | 18 |

5 7 8 | 9 10 13 | 14 16 | 18 19 20 |

Delete: 13
14 |

9 | 18 |

5 7 8 | 9 10 | 14 16 | 18 19 20 |

Delete: 14
Leaf underflow
Leaf borrow from right
16 |

9 | 19 |

5 7 8 | 9 10 | 16 18 | 19 20 |

Delete: 5
16 |

9 | 19 |

7 8 | 9 10 | 16 18 | 19 20 |

Dele

10 18 |

5 7 | 14 16 | 20 22 |

0 1 4 | 5 6 | 7 8 | 10 12 13 | 14 15 | 16 17 | 18 19 | 20 21 | 22 23 |

Delete: 19
Leaf underflow
Leaf merge with right
10 18 |

5 7 | 14 16 | 22 |

0 1 4 | 5 6 | 7 8 | 10 12 13 | 14 15 | 16 17 | 18 20 21 | 22 23 |

Delete: 17
Leaf underflow
Leaf merge with left
10 18 |

5 7 | 14 | 22 |

0 1 4 | 5 6 | 7 8 | 10 12 13 | 14 15 16 | 18 20 21 | 22 23 |

Delete: 22
Leaf underflow
Leaf borrow from left
10 18 |

5 7 | 14 | 21 |

0 1 4 | 5 6 | 7 8 | 10 12 13 | 14 15 16 | 18 20 | 21 23 |

Delete: 13
10 18 |

5 7 | 14 | 21 |

0 1 4 | 5 6 | 7 8 | 10 12 | 14 15 16 | 18 20 | 21 23 |

Delete: 15
10 18 |

5 7 | 14 | 21 |

0 1 4 | 5 6 | 7 8 | 10 12 | 14 16 | 18 20 | 21 23 |

Delete: 8
Leaf underflow
Leaf merge with left
10 18 |

5 | 14 | 21 |

0 1 4 | 5 6 7 | 10 12 | 14 16 | 18 20 | 21 23 |

Delete: 0
10 18 |

5 | 14 | 21 |

1 4 | 5 6 7 | 10 12 | 14 16 | 18 20 | 21 23 |

Delete: 23
Leaf underflow
Leaf merge with left
Non leaf underflow
Non leaf merge with left
10 |

5 | 

...

Delete: 16
Leaf underflow
Leaf borrow from left
5 |

0 2 | 5 6 |

Delete: 5
Leaf underflow
Leaf merge with left
root has no keys, updating root!
0 2 6 |

Delete: 6
0 2 |

Delete: 0
2 |

Delete: 2
tree is empty
|

insertion: [15, 8, 13, 19, 9, 23, 2, 6, 4, 21, 22, 7, 5, 20, 3, 17, 0, 12, 11, 10, 18, 1, 14, 16]
deletion: [20, 2, 4, 21, 18, 19, 10, 22, 0, 11, 12, 15, 8, 23, 3, 6, 14, 1, 7, 16, 9, 13, 17, 5]
Delete: 20
Leaf underflow
Leaf borrow from right
9 15 |

2 4 6 | 12 | 17 19 22 |

0 1 | 2 3 | 4 5 | 6 7 8 | 9 10 11 | 12 13 14 | 15 16 | 17 18 | 19 21 | 22 23 |

Delete: 2
Leaf underflow
Leaf merge with left
9 15 |

4 6 | 12 | 17 19 22 |

0 1 3 | 4 5 | 6 7 8 | 9 10 11 | 12 13 14 | 15 16 | 17 18 | 19 21 | 22 23 |

Delete: 4
Leaf underflow
Leaf borrow from left
9 15 |

3 6 | 12 | 17 19 22 |

0 1 | 3 5 | 6 7 8 | 9 10 11 | 12 13 14 | 15 16 | 17 18 | 19 21 | 22 23 |

Delete: 21
Leaf underflow
Leaf merge with left
9 15 |

3 6 | 12 | 17 22 |

0 1 | 3 5 | 6 7 8 | 9 10 11 | 12 13 14 | 15 16 | 1

6 | 10 12 | 22 |

1 3 5 | 6 7 | 8 9 | 10 11 | 12 13 16 | 18 19 20 | 22 23 |

Delete: 12
8 18 |

6 | 10 13 | 22 |

1 3 5 | 6 7 | 8 9 | 10 11 | 13 16 | 18 19 20 | 22 23 |

Delete: 22
Leaf underflow
Leaf borrow from left
8 18 |

6 | 10 13 | 20 |

1 3 5 | 6 7 | 8 9 | 10 11 | 13 16 | 18 19 | 20 23 |

Delete: 13
Leaf underflow
Leaf merge with left
8 18 |

6 | 10 | 20 |

1 3 5 | 6 7 | 8 9 | 10 11 16 | 18 19 | 20 23 |

Delete: 7
Leaf underflow
Leaf borrow from left
8 18 |

5 | 10 | 20 |

1 3 | 5 6 | 8 9 | 10 11 16 | 18 19 | 20 23 |

Delete: 23
Leaf underflow
Leaf merge with left
Non leaf underflow
Non leaf merge with left
8 |

5 | 10 18 |

1 3 | 5 6 | 8 9 | 10 11 16 | 18 19 20 |

Delete: 5
Leaf underflow
Leaf merge with left
Non leaf underflow
Non leaf borrow from right
10 |

8 | 18 |

1 3 6 | 8 9 | 10 11 16 | 18 19 20 |

Delete: 6
10 |

8 | 18 |

1 3 | 8 9 | 10 11 16 | 18 19 20 |

Delete: 8
Leaf underflow
Leaf merge with left
Non leaf underflow
Non leaf merge with right
root has no keys, upda

Non leaf underflow
Non leaf merge with right
root has no keys, updating root!
14 19 |

6 7 8 | 14 18 | 19 22 |

Delete: 7
14 19 |

6 8 | 14 18 | 19 22 |

Delete: 14
Leaf underflow
Leaf merge with left
19 |

6 8 18 | 19 22 |

Delete: 22
Leaf underflow
Leaf borrow from left
18 |

6 8 | 18 19 |

Delete: 6
Leaf underflow
Leaf merge with right
root has no keys, updating root!
8 18 19 |

Delete: 8
18 19 |

Delete: 19
18 |

Delete: 18
tree is empty
|

insertion: [11, 7, 3, 6, 15, 16, 2, 10, 19, 12, 5, 8, 21, 0, 4, 23, 1, 14, 18, 20, 13, 22, 17, 9]
deletion: [3, 16, 2, 17, 23, 9, 13, 5, 21, 4, 7, 20, 1, 10, 15, 6, 19, 22, 14, 8, 0, 12, 11, 18]
Delete: 3
Leaf underflow
Leaf borrow from left
7 11 19 |

2 5 | 9 | 13 15 17 | 21 |

0 1 | 2 4 | 5 6 | 7 8 | 9 10 | 11 12 | 13 14 | 15 16 | 17 18 | 19 20 | 21 22 23 |

Delete: 16
Leaf underflow
Leaf merge with left
7 11 19 |

2 5 | 9 | 13 17 | 21 |

0 1 | 2 4 | 5 6 | 7 8 | 9 10 | 11 12 | 13 14 15 | 17 18 | 19 20 | 21 22 23 |

Delete: 2
Leaf underflow
Lea

Leaf underflow
Leaf merge with right
Non leaf underflow
Non leaf borrow from left
5 13 |

3 | 7 | 19 |

0 1 2 | 3 4 | 5 6 | 7 10 12 | 13 15 17 | 19 22 23 |

Delete: 2
5 13 |

3 | 7 | 19 |

0 1 | 3 4 | 5 6 | 7 10 12 | 13 15 17 | 19 22 23 |

Delete: 10
5 13 |

3 | 7 | 19 |

0 1 | 3 4 | 5 6 | 7 12 | 13 15 17 | 19 22 23 |

Delete: 13
5 15 |

3 | 7 | 19 |

0 1 | 3 4 | 5 6 | 7 12 | 15 17 | 19 22 23 |

Delete: 5
Leaf underflow
Leaf merge with right
Non leaf underflow
Non leaf merge with left
15 |

3 6 | 19 |

0 1 | 3 4 | 6 7 12 | 15 17 | 19 22 23 |

Delete: 3
Leaf underflow
Leaf borrow from right
15 |

4 7 | 19 |

0 1 | 4 6 | 7 12 | 15 17 | 19 22 23 |

Delete: 17
Leaf underflow
Leaf borrow from right
15 |

4 7 | 22 |

0 1 | 4 6 | 7 12 | 15 19 | 22 23 |

Delete: 19
Leaf underflow
Leaf merge with right
Non leaf underflow
Non leaf borrow from left
7 |

4 | 15 |

0 1 | 4 6 | 7 12 | 15 22 23 |

Delete: 22
7 |

4 | 15 |

0 1 | 4 6 | 7 12 | 15 23 |

Delete: 15
Leaf underflow
Leaf merge with left
Non

KeyboardInterrupt: 